In [1]:
import os
import trimesh
import numpy as np
from IPython.display import display
from trimesh.graph import split as graph_split
# import networkx
import scipy


# Load and clean original mesh

In [2]:
# 1. Load the mesh
mesh_path = "D:\\sunny\\Codes\\IIB_project\\data\\6_CT_data\\micro_ct\\micro_ct_mesh_center.ply"
mesh = trimesh.load(mesh_path)
# Display the mesh
display(mesh.show())
assert isinstance(mesh, trimesh.Trimesh), "The loaded object is not a Trimesh object."
print(f"Loaded mesh with {len(mesh.vertices)} vertices and {len(mesh.faces)} faces.")




Loaded mesh with 133881 vertices and 264707 faces.


In [3]:
# # 2. Clean Mesh: Remove Small Noise Components
# # Split the mesh into connected components, then keep only those whose volume is
# # above a specified fraction of the largest component to preserve multiple main parts.
# # Build adjacency list for faces
# adjacent = {i: set() for i in range(len(mesh.faces))}
# for f1, f2 in mesh.face_adjacency:
#     adjacent[f1].add(f2)
#     adjacent[f2].add(f1)

# # BFS to extract connected face groups
# visited = set()
# components_faces = []
# for i in range(len(mesh.faces)):
#     if i in visited:
#         continue
#     stack = [i]
#     comp_faces = []
#     while stack:
#         curr = stack.pop()
#         if curr in visited:
#             continue
#         visited.add(curr)
#         comp_faces.append(curr)
#         stack.extend(adjacent[curr] - visited)
#     components_faces.append(comp_faces)

# # Build submeshes manually, preserving vertex colors
# submeshes = []
# for comp in components_faces:
#     faces = mesh.faces[comp]
#     unique_verts, inverse = np.unique(faces.reshape(-1), return_inverse=True)
#     new_vertices = mesh.vertices[unique_verts]
#     new_faces = inverse.reshape(-1, 3)
#     if hasattr(mesh.visual, 'vertex_colors'):
#         new_colors = mesh.visual.vertex_colors[unique_verts]
#         sub = trimesh.Trimesh(vertices=new_vertices, faces=new_faces,
#                               process=False, vertex_colors=new_colors)
#     else:
#         sub = trimesh.Trimesh(vertices=new_vertices, faces=new_faces, process=False)
#     submeshes.append(sub)

# # Drop the three smallest components by vertex count
# submeshes_sorted = sorted(submeshes, key=lambda m: len(m.vertices))
# num_comp_discarded = 14
# kept = submeshes_sorted[num_comp_discarded:]

# # Concatenate kept components
# mesh_clean = trimesh.util.concatenate(kept)
# mesh_clean.remove_unreferenced_vertices()
# print(f"Dropped 3 smallest components; kept {len(kept)} parts")
# print(f"Cleaned mesh: {len(mesh_clean.vertices)} vertices, {len(mesh_clean.faces)} faces")

# # Display the cleaned mesh
# display(mesh_clean.show())
mesh_clean = mesh


# Offset outwards

In [4]:
# 3. Define Offset Parameters
offsets = [0.5, 1.0]        # in mesh units
alphas = [175, 100]         # 0-255 opacity

directions = ['outward']    # use ['outward','inward'] for ± envelope

In [7]:
# 4. Generate Offset Shells
normals = mesh_clean.vertex_normals
shells = []
for offset, alpha in zip(offsets, alphas):
    for direction in directions:
        sign = 1 if direction=='outward' else -1
        verts = mesh_clean.vertices + normals*(sign*offset)
        shell = trimesh.Trimesh(vertices=verts, faces=mesh_clean.faces, process=False)
        # preserve no color on shells, but you could copy original colors if desired
        color = mesh_clean.visual.vertex_colors.copy()
        color[:, 3] = alpha
        shell.visual.vertex_colors = color
        shells.append((shell, direction, offset))

display(f"Generated {len(shells)} shells: {[(d,o) for _,d,o in shells]}")

"Generated 2 shells: [('outward', 0.5), ('outward', 1.0)]"

In [15]:
# 5. Visualize Inline
scene = trimesh.Scene([s for s,_,_ in shells])
scene.show()

# 6. Save Shells to PLY
output_dir = os.path.join(os.path.dirname(mesh_path), 'shells')
os.makedirs(output_dir, exist_ok=True)
for shell, direction, offset in shells:
    filename = os.path.join(output_dir, f"shell_{direction}_{offset}.ply")
    shell.export(filename)
    print(f"Saved {filename}")
    

Saved D:\sunny\Codes\IIB_project\data\6_CT_data\micro_ct\shells\shell_outward_0.5.ply
Saved D:\sunny\Codes\IIB_project\data\6_CT_data\micro_ct\shells\shell_outward_1.0.ply
